In [1]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col,upper,udf,element_at,explode,regexp_replace
from pyspark.sql.types import StringType, DateType

spark = SparkSession \
    .builder \
    .appName("Spark Cassandra Connector with Python") \
    .config("spark.sql.extensions", "com.datastax.spark.connector.CassandraSparkExtensions") \
    .getOrCreate()
keyspace = "mycatalog.testks"
spark.conf.set("spark.sql.catalog.mycatalog", "com.datastax.spark.connector.datasource.CassandraCatalog")

In [2]:
spark.sql("CREATE DATABASE IF NOT EXISTS mycatalog.testks WITH DBPROPERTIES (class='SimpleStrategy',replication_factor='1')")
spark.sql("CREATE TABLE IF NOT EXISTS mycatalog.testks.testtable1 (key1 STRING, value1 STRING) USING cassandra PARTITIONED BY (key1)")
spark.sql("CREATE TABLE IF NOT EXISTS mycatalog.testks.testtable2 (key2 STRING, value2 STRING) USING cassandra PARTITIONED BY (key2)")

DataFrame[]

In [3]:
test_table1_df = spark.createDataFrame([("a#hidden", 1), ("b#hidden", 2), ("c#hidden",  3)], ["key1", "value1"])
test_table2_df = spark.createDataFrame([("a", 12), ("b", 13), ("c",  14)], ["key2", "value2"])
test_table1_df.write\
    .format("org.apache.spark.sql.cassandra")\
    .mode('append')\
    .options(table="testtable1", keyspace="testks")\
    .save()
test_table2_df.write\
    .format("org.apache.spark.sql.cassandra")\
    .mode('append')\
    .options(table="testtable2", keyspace="testks")\
    .save()



In [4]:
test_table1_df = spark.read.table(keyspace + ".testtable1")
test_table2_df = spark.read.table(keyspace + ".testtable2")

test_table1_df.show()
test_table2_df.show()

+--------+------+
|    key1|value1|
+--------+------+
|c#hidden|     3|
|a#hidden|     1|
|b#hidden|     2|
+--------+------+

+----+------+
|key2|value2|
+----+------+
|   b|    13|
|   a|    12|
|   c|    14|
+----+------+



In [5]:
test_table1_df = test_table1_df.select(regexp_replace(col("key1"), "#hidden", "").alias("key1"), "value1")
test_table1_df.show()

+----+------+
|key1|value1|
+----+------+
|   a|     1|
|   c|     3|
|   b|     2|
+----+------+



In [6]:
test_table1_df.join(test_table2_df, test_table1_df.key1 == test_table2_df.key2).show()

Py4JJavaError: An error occurred while calling o102.showString.
: scala.MatchError: regexp_replace(key1#16, #hidden, ) AS key1#46 (of class org.apache.spark.sql.catalyst.expressions.Alias)
	at org.apache.spark.sql.cassandra.execution.CassandraDirectJoinStrategy$.$anonfun$aliasMap$1(CassandraDirectJoinStrategy.scala:315)
	at scala.collection.TraversableLike.$anonfun$map$1(TraversableLike.scala:238)
	at scala.collection.mutable.ResizableArray.foreach(ResizableArray.scala:62)
	at scala.collection.mutable.ResizableArray.foreach$(ResizableArray.scala:55)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:49)
	at scala.collection.TraversableLike.map(TraversableLike.scala:238)
	at scala.collection.TraversableLike.map$(TraversableLike.scala:231)
	at scala.collection.AbstractTraversable.map(Traversable.scala:108)
	at org.apache.spark.sql.cassandra.execution.CassandraDirectJoinStrategy$.aliasMap(CassandraDirectJoinStrategy.scala:315)
	at org.apache.spark.sql.cassandra.execution.C

In [7]:
df_1 = spark.createDataFrame([("a#hidden", 1), ("b#hidden", 2), ("c#hidden",  3)], ["id", "value"])
df_2 = spark.createDataFrame([("a", 12), ("b", 13), ("c",  14)], ["otherId", "someOtherValue"])
df_1 = df_1.select(regexp_replace(col("id"), "#hidden", "").alias("id"), col("value"))
df_1.show()
df_1.join(df_2, df_1.id == df_2.otherId).show()







+---+-----+
| id|value|
+---+-----+
|  a|    1|
|  b|    2|
|  c|    3|
+---+-----+

+---+-----+-------+--------------+
| id|value|otherId|someOtherValue|
+---+-----+-------+--------------+
|  c|    3|      c|            14|
|  b|    2|      b|            13|
|  a|    1|      a|            12|
+---+-----+-------+--------------+

